In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import r2_score
import pandas as pd
import numpy as np
import copy



In [2]:
#Extract mean absolute error, R2, and other perfomance metrics for phenoclimate models developed using data from each simulated species while also recording the attributes of each species

def Onset_termination_eval(out_path, model_dict, sample_counts = [100,200,300,400,500,600,700,800,900,1000,2000,3000,4000,5000], taxon_column = 'genus_species', min_samples = 100, sample_type = ''):
    
    '''
    :param: out_path: path to output results
    :param model_dict:  dictionary listing the aspect of phenological timing (population, individual, etc.) being evaluated vs. predictions, as well as a list including:
            A) a list of model permutations to be included (from models developed using prior R code),
            B) the name of the data column containing the predicted  phenological data to be compared to raw simulations, with the percentile rank replaced by 'YYY'
            C) a list of the percentile ranks to be evaluated (always ['0.1', '0.5', '0.9'] in this study)
            D) a list of the column names to be compared to predicted DOYs
                               
    :param sample_counts: list of the number of specimens used in training the models being evaluated
    :param taxon_column: string consisting of the name of the column used to delineate simulated speices
    :min_samples: int delieating the minimum number of samples required to be evaluated in the model
    :sample_type: string delieating sample type
    
   Generates a series of files recording the MAE, R2, RMSE, and raw error of predictions generated from models of each simulated species trained using the numbers of specimens listed in sample_counts as csvs. 
    '''
    
    mae_frame = 0 
    r2_concat = 'blank'
    mae_concat = 'blank'
    rmse_concat = 'blank'
    
    
    
    for iter_sampleCount in sample_counts:
        
            
    
        for iter_model in model_dict:
            print("__________________________" + iter_model + '____________________________________')
            actual_columns =  model_dict[iter_model][3]
            early_column = actual_columns[0]
            mid_column = actual_columns[1]
            late_column = actual_columns[2]

            
            if type(model_dict[iter_model][0]) == str:
                iter_path = model_dict[iter_model][0]
                iter_data = pd.read_csv(iter_path.replace('XXX', str(iter_sampleCount)))
                print(iter_path)
            
            elif type(model_dict[iter_model][0]) == list:
                
                iter_path = model_dict[iter_model][0]
                iter_data = 'blank'
                
                for iter_iter_path in iter_path:
                
                    iter_iter_data = pd.read_csv(iter_iter_path.replace('XXX', str(iter_sampleCount)))
                    print(iter_iter_path)
                    if "variablesigma" in iter_iter_path:
                        iter_iter_data['sigma'] = -9999.0
                        
                        
                    if "variablesigma" in iter_iter_path:
                        iter_iter_data['sigma'] = -9999.0
                        
                        
                    if "variableduration" in iter_iter_path:
                        iter_iter_data['duration'] = -9999.0
                    
                    if type(iter_data) == str:
                        iter_data = copy.deepcopy(iter_iter_data)
                    else:
                        iter_data = pd.concat([iter_data, iter_iter_data])
            
            pred_column_base = model_dict[iter_model][1]
            quantiles = model_dict[iter_model][2]
            print(quantiles)




            #get sample counts for each species, cull data to species with >- min samples number of observations
            #sample_count = iter_data.groupby(taxon_column).size()
            #sample_count = sample_count.to_frame()
            #sample_count.columns = ['sample_count']
            #iter_data = pd.merge(iter_data, sample_count, on = [taxon_column])
            #iter_data = iter_data[iter_data['sample_count']>= min_samples]


            #remove rows with NAs or infinites
            iter_data.replace([np.inf, -np.inf], np.nan, inplace=True)
            iter_data.dropna(how="any", inplace = True)
            iter_data.reset_index(inplace = True, drop = True)


            if type(mae_frame) == int:
                mae_frame = pd.DataFrame({'genus_species': pd.unique(iter_data[taxon_column])})
                mae_frame.set_index(['genus_species'], drop = True, inplace = True)

                rmse_frame = pd.DataFrame({'genus_species': pd.unique(iter_data[taxon_column])})
                rmse_frame.set_index(['genus_species'], drop = True, inplace = True)

                r2_frame = pd.DataFrame({'genus_species': pd.unique(iter_data[taxon_column])})
                r2_frame.set_index(['genus_species'], drop = True, inplace = True)
                
                raw_error_frame = pd.DataFrame({'genus_species': pd.unique(iter_data[taxon_column])})
                raw_error_frame.set_index(['genus_species'], drop = True, inplace = True)
                #print(mae_frame)

            for iter_species in pd.unique(iter_data[taxon_column]):
                #print(iter_species)
                species_data = iter_data[iter_data[taxon_column] == iter_species]
                sample_count_iter = len(species_data)

                rmse_frame.at[iter_species, "sample_count"] = len(species_data)
                mae_frame.at[iter_species, "sample_count"] = len(species_data)
                r2_frame.at[iter_species, "sample_count"] = len(species_data)
                raw_error_frame.at[iter_species, "sample_count"] = len(species_data)
                
                rmse_frame.at[iter_species, "slope"] = species_data["slope"].mean()
                mae_frame.at[iter_species, "slope"] = species_data["slope"].mean()
                r2_frame.at[iter_species, "slope"] = species_data["slope"].mean()
                raw_error_frame.at[iter_species, "slope"] = species_data["slope"].mean()
                
                
                rmse_frame.at[iter_species, "sigma"] = species_data["sigma"].mean()
                mae_frame.at[iter_species, "sigma"] = species_data["sigma"].mean()
                r2_frame.at[iter_species, "sigma"] = species_data["sigma"].mean()
                raw_error_frame.at[iter_species, "sigma"] = species_data["sigma"].mean()
                
                rmse_frame.at[iter_species, "duration"] = species_data["duration"].mean()
                mae_frame.at[iter_species, "duration"] = species_data["duration"].mean()
                r2_frame.at[iter_species, "duration"] = species_data["duration"].mean()
                raw_error_frame.at[iter_species, "duration"] = species_data["duration"].mean()
                

                species_RMSE_Onset_Pred = mean_squared_error(species_data[early_column], species_data[pred_column_base.replace('YYY', quantiles[0])])
                species_MAE_Onset_Pred = mean_absolute_error(species_data[early_column], species_data[pred_column_base.replace('YYY', quantiles[0])])
                species_R2_Onset_Pred = r2_score(species_data[early_column], species_data[pred_column_base.replace('YYY', quantiles[0])])
                species_raw_error_Onset_Pred =  species_data[pred_column_base.replace('YYY', quantiles[0])].mean() - species_data[early_column].mean()
                rmse_frame.at[iter_species, "RMSE_" + iter_model + "_Onset_inferred"] = species_RMSE_Onset_Pred
                mae_frame.at[iter_species, "MAE_" +iter_model + "_Onset_inferred"] = species_MAE_Onset_Pred
                r2_frame.at[iter_species, "R2_" +iter_model + "_Onset_inferred"] = species_R2_Onset_Pred
                raw_error_frame.at[iter_species, "raw_error_" +iter_model + "_Onset_inferred"] = species_raw_error_Onset_Pred

                species_RMSE_middle_Pred = mean_squared_error(species_data[mid_column], species_data[pred_column_base.replace('YYY', quantiles[1])])
                species_MAE_middle_Pred = mean_absolute_error(species_data[mid_column], species_data[pred_column_base.replace('YYY', quantiles[1])])
                species_R2_middle_Pred = r2_score(species_data[mid_column], species_data[pred_column_base.replace('YYY', quantiles[1])])
                species_raw_error_middle_Pred =  species_data[pred_column_base.replace('YYY', quantiles[1])].mean() - species_data[mid_column].mean()
                rmse_frame.at[iter_species, "RMSE_" + iter_model + "_Median_inferred"] = species_RMSE_middle_Pred
                mae_frame.at[iter_species, "MAE_" +iter_model + "_Median_inferred"] = species_MAE_middle_Pred
                r2_frame.at[iter_species, "R2_" +iter_model + "_Median_inferred"] = species_R2_middle_Pred
                raw_error_frame.at[iter_species, "raw_error_" +iter_model + "_Median_inferred"] = species_raw_error_middle_Pred

                species_RMSE_Termination_Pred = mean_squared_error(species_data[late_column], species_data[pred_column_base.replace('YYY', quantiles[2])])
                species_MAE_Termination_Pred = mean_absolute_error(species_data[late_column], species_data[pred_column_base.replace('YYY', quantiles[2])])
                species_R2_Termination = r2_score(species_data[late_column], species_data[pred_column_base.replace('YYY', quantiles[2])])
                species_raw_error_Termination_Pred =  species_data[pred_column_base.replace('YYY', quantiles[2])].mean() - species_data[late_column].mean()
                rmse_frame.at[iter_species, "RMSE_" + iter_model + "_Termination_inferred"] = species_RMSE_Termination_Pred
                mae_frame.at[iter_species, "MAE_" +iter_model + "_Termination_inferred"] = species_MAE_Termination_Pred
                r2_frame.at[iter_species, "R2_" +iter_model + "_Termination_inferred"] = species_R2_Termination
                raw_error_frame.at[iter_species, "raw_error_" +iter_model + "_Termination_inferred"] = species_raw_error_Termination_Pred

            #r2_frame.to_csv(out_path +  'Overall_R2' + str(iter_sampleCount) + '.csv')
            #mae_frame.to_csv(out_path + 'Overall_mae' + str(iter_sampleCount) + '.csv')
            #rmse_frame.to_csv(out_path + 'Overall_rmse' + str(iter_sampleCount) + '.csv')

        if type(r2_concat) == str:
            r2_concat = copy.deepcopy(r2_frame)
            mae_concat = copy.deepcopy(mae_frame)
            rmse_concat = copy.deepcopy(rmse_frame)
            raw_error_concat = copy.deepcopy(raw_error_frame)
        else:
            r2_concat = pd.concat([r2_concat, copy.deepcopy(r2_frame)])
            mae_concat = pd.concat([mae_concat, copy.deepcopy(mae_frame)])
            rmse_concat = pd.concat([rmse_concat, copy.deepcopy(rmse_frame)])
            raw_error_concat = pd.concat([raw_error_concat, copy.deepcopy(raw_error_frame)])
    
    r2_concat['Sample_Type'] = sample_type
    mae_concat['Sample_Type'] = sample_type
    rmse_concat['Sample_Type'] = sample_type
    raw_error_concat['Sample_Type'] = sample_type
    
    r2_concat.to_csv(out_path +  'Overall_R2_multiSampleCounts.csv')
    mae_concat.to_csv(out_path + 'Overall_mae_multiSampleCounts.csv')
    rmse_concat.to_csv(out_path + 'Overall_rmse_multiSampleCounts.csv') 
    raw_error_concat.to_csv(out_path + 'Overall_raw_multiSampleCounts.csv') 
    
    return [mae_concat, rmse_concat, r2_concat]

In [3]:
#create summary estimates of accuracy for models constructed using skews towards collections of individuals proximate to their (individual) mean flowering date

model_dict = {'indiv_timing': [["Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                                "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv"],
                               'RQ_Pred_YYY_Local_sample', ['0.1', '0.5', '0.9'], 
                               ['Local_indiv_onset_DOY', 'Local_indiv_mean_DOY', 'Local_indiv_termination_DOY']],
             'Population_mean_timing': [["Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                                "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv"],
                               'RQ_Pred_YYY_Local_sample', ['0.1', '0.5', '0.9'],
                               ['Local_10pct_mean_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_mean_DOY']],
'Population_timing': [["Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                                "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv"],
                              'RQ_Pred_YYY_Local_sample', ['0.1', '0.5', '0.9'],         
                              ['Local_10pct_onset_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_termination_DOY']]}

summary_list = Onset_termination_eval(out_path = "Data/Simulated_Distribution_Models/Summaries/", 
                                      model_dict = model_dict,
                                     sample_counts = [100, 200, 300, 400, 500, 600, 700, 800, 900, 1000], sample_type = 'normal')
summary_data = summary_list[0]
r2_summary = summary_list[2]

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_RQ_Predict_Test_simData_Sim

__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_RQ_Predict_Test_s

['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_RQ_Predict_Test_simData_Sim

__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_RQ_Predict_Test_s

__________________________Population_timing____________________________________
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_RQ_Predict_Test_simDat

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_RQ_Predict_Test_simData_Sim

__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data/Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_RQ_Predict_Test_s

In [4]:
#create summary estimates of accuracy for models constructed using skews towards collections of individuals proximate to their (individual) flowering termination date

model_dict = {'indiv_timing': [["Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                                "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv"],
                               'RQ_Pred_YYY_Local_sample_rightDist', ['0.1', '0.5', '0.9'], 
                               ['Local_indiv_onset_DOY', 'Local_indiv_mean_DOY', 'Local_indiv_termination_DOY']],
             'Population_mean_timing': [["Data\Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                                "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv"],
                               'RQ_Pred_YYY_Local_sample_rightDist', ['0.1', '0.5', '0.9'],
                               ['Local_10pct_mean_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_mean_DOY']],
'Population_timing': [["Data\Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                                "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv"],
                              'RQ_Pred_YYY_Local_sample_rightDist', ['0.1', '0.5', '0.9'],         
                              ['Local_10pct_onset_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_termination_DOY']]}

summary_list = Onset_termination_eval(out_path = "Data/Simulated_Distribution_Models/Summaries/RightDist_", 
                                      model_dict = model_dict,
                                     sample_counts = [100, 200, 300, 400, 500, 600, 700, 800, 900, 1000], sample_type = 'right_skew')
summary_data = summary_list[0]
r2_summary = summary_list[2]

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_Sl

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distrib

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
['0.1', '0.5', '0.9']
__________________________Population_mean_timing____________________________________
Data\Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightD

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
[

['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data\Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_RQ_Predict_Test_simDat

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distrib

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
['0.1', '0.5', '0.9']
__________________________indiv_timing____________________________________
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Mo

In [5]:
q = pd.read_csv('Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_100_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv')
q.head()

Unnamed: 0  unique_ID                                      genus_species  \
0           1      30846  Taxon_101.0_Ann_tmean_13_10_151.0_Ann_tmean_13...   
1           2      40764  Taxon_101.0_Ann_tmean_13_10_151.0_Ann_tmean_13...   
2           3      28032  Taxon_101.0_Ann_tmean_13_10_151.0_Ann_tmean_13...   
3           4      26648  Taxon_101.0_Ann_tmean_13_10_151.0_Ann_tmean_13...   
4           5       2324  Taxon_101.0_Ann_tmean_13_10_151.0_Ann_tmean_13...   

   slope         param  sigma  duration  Local_10pct_mean_DOY  \
0      1  Ann_tmean_13     10        15                    43   
1      1  Ann_tmean_13     10        15                    54   
2      1  Ann_tmean_13     10        15                    49   
3      1  Ann_tmean_13     10        15                    50   
4      1  Ann_tmean_13     10        15                    48   

   Local_50pct_mean_DOY  Local_90pct_mean_DOY  ...  Local_indiv_mean_DOY  \
0             55.585250                    68  ...                    52   
1             66.810668                    80  ...                    73   
2             62.110167                    75  ...                    56   
3             62.930584                    76  ...                    58   
4             61.216167                    74  ...                    60   

   Local_indiv_onset_DOY  Local_indiv_termination_DOY   Latitude   Longitude  \
0                     44                           60  44.416667 -106.291667   
1                     66                           80  34.833333  -88.375000   
2                     48                           64  37.791667  -84.458333   
3                     50                           66  37.166667 -101.750000   
4                     52                           68  41.791667  -72.541667   

   First_Yes_Year  Local_sample_rightDist  RQ_Pred_0.1_Local_sample_rightDist  \
0            1993                      59                           43.636772   
1            2007                      74                           57.811344   
2            1989                      60                           51.875923   
3            1987                      57                           52.911881   
4            1953                      57                           50.747050   

   RQ_Pred_0.5_Local_sample_rightDist  RQ_Pred_0.9_Local_sample_rightDist  
0                           59.000000                           72.012669  
1                           68.111266                           85.886909  
2                           64.296039                           80.077248  
3                           64.961942                           81.091256  
4                           63.570412                           78.972294  

[5 rows x 23 columns]

In [6]:
#create summary estimates of accuracy for models constructed using skews towards collections of individuals proximate to their (individual) flowering onset date

model_dict = {'indiv_timing': [["Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                                "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv"],
                               'RQ_Pred_YYY_Local_sample_leftDist', ['0.1', '0.5', '0.9'], 
                               ['Local_indiv_onset_DOY', 'Local_indiv_mean_DOY', 'Local_indiv_termination_DOY']],
             'Population_mean_timing': [["Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                                "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv"],
                               'RQ_Pred_YYY_Local_sample_leftDist', ['0.1', '0.5', '0.9'],
                               ['Local_10pct_mean_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_mean_DOY']],
'Population_timing': [["Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                                "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv"],
                              'RQ_Pred_YYY_Local_sample_leftDist', ['0.1', '0.5', '0.9'],         
                              ['Local_10pct_onset_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_termination_DOY']]}

summary_list = Onset_termination_eval(out_path = "Data/Simulated_Distribution_Models/Summaries/LeftDist_", 
                                      model_dict = model_dict,
                                     sample_counts = [100, 200, 300, 400, 500, 600, 700, 800, 900, 1000], sample_type = 'left_skew')
summary_data = summary_list[0]
r2_summary = summary_list[2]

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
['0.1', '0.5', '0.9']
__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_RQ_Predict_Te

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
['0.1', '0.5', '

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_

In [7]:
#create summary estimates of accuracy for models constructed using skews towards collections of individuals with no collection bias

model_dict = {'indiv_timing': [["Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                                "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv"],
                               'RQ_Pred_YYY_Local_sample_flatDist', ['0.1', '0.5', '0.9'], 
                               ['Local_indiv_onset_DOY', 'Local_indiv_mean_DOY', 'Local_indiv_termination_DOY']],
             'Population_mean_timing': [["Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                                "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv"],
                               'RQ_Pred_YYY_Local_sample_flatDist', ['0.1', '0.5', '0.9'],
                               ['Local_10pct_mean_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_mean_DOY']],
'Population_timing': [["Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                                "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv"],
                              'RQ_Pred_YYY_Local_sample_flatDist', ['0.1', '0.5', '0.9'],         
                              ['Local_10pct_onset_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_termination_DOY']]}

summary_list = Onset_termination_eval(out_path = "Data/Simulated_Distribution_Models/Summaries/FlatDist_", 
                                      model_dict = model_dict,
                                     sample_counts = [100, 200, 300, 400, 500, 600, 700, 800, 900, 1000], sample_type = 'flat_skew')
summary_data = summary_list[0]
r2_summary = summary_list[2]

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
['0.1', '0.5', '0.9']
__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_RQ_Predict_Test_simDat

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_RQ_Predict_Test_si

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
['0.1', '0.5', '0.9']
__________________________indiv_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predi

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
['0.1', '0.5', '

In [8]:
#create summary data files documenting the r2, mae, rmse, and raw error of phenoclimate predictions created from data exhibiting each form of indivudal collection bias

flat_r2 = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/FlatDist_Overall_R2_multiSampleCounts.csv')
flat_mae = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/FlatDist_Overall_mae_multiSampleCounts.csv')
flat_rmse = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/FlatDist_Overall_rmse_multiSampleCounts.csv')
flat_raw = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/FlatDist_Overall_raw_multiSampleCounts.csv')
print(len(flat_r2))

normal_r2 = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/Overall_R2_multiSampleCounts.csv')
normal_mae = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/Overall_mae_multiSampleCounts.csv')
normal_rmse = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/Overall_rmse_multiSampleCounts.csv')
normal_raw = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/Overall_raw_multiSampleCounts.csv')
print(len(normal_r2))

left_r2 = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/LeftDist_Overall_R2_multiSampleCounts.csv')
left_mae = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/LeftDist_Overall_mae_multiSampleCounts.csv')
left_rmse = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/LeftDist_Overall_rmse_multiSampleCounts.csv')
left_raw = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/LeftDist_Overall_raw_multiSampleCounts.csv')
print(len(left_r2))

right_r2 = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/RightDist_Overall_R2_multiSampleCounts.csv')
right_mae = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/RightDist_Overall_mae_multiSampleCounts.csv')
right_rmse = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/RightDist_Overall_rmse_multiSampleCounts.csv')
right_raw = pd.read_csv('Data/Simulated_Distribution_Models/Summaries/RightDist_Overall_raw_multiSampleCounts.csv')
print(len(right_r2))

R2_all = pd.concat([normal_r2, flat_r2, left_r2, right_r2], axis = 0)
MAE_all = pd.concat([normal_mae, flat_mae, left_mae, right_mae], axis = 0)
RMSE_all = pd.concat([normal_rmse, flat_rmse, left_rmse, right_rmse], axis = 0)
Raw_all = pd.concat([normal_raw, flat_raw, left_raw, right_raw], axis = 0)

R2_all.to_csv('Data/Simulated_Distribution_Models/Summaries/AllSamples_Overall_R2_multiSampleCounts.csv')
MAE_all.to_csv('Data/Simulated_Distribution_Models/Summaries/AllSamples_Overall_MAE_multiSampleCounts.csv')
RMSE_all.to_csv('Data/Simulated_Distribution_Models/Summaries/AllSamples_Overall_RMSE_multiSampleCounts.csv')
Raw_all.to_csv('Data/Simulated_Distribution_Models/Summaries/AllSamples_Overall_raw_multiSampleCounts.csv')

15000
15000
15000
15000


In [13]:
########################
#######
#create summary estimates of accuracy for models constructed using s individuals with mild noise in the phenological variation in population median flowering dates
#and a bias towards collection of specimens proximate to theire individual mean flowering date


model_dict = {'indiv_timing': [["Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                                "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv"],
                               'RQ_Pred_YYY_Local_sample', ['0.1', '0.5', '0.9'], 
                               ['Local_indiv_onset_DOY', 'Local_indiv_mean_DOY', 'Local_indiv_termination_DOY']],
             'Population_mean_timing': [["Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                                "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv"],
                               'RQ_Pred_YYY_Local_sample', ['0.1', '0.5', '0.9'],
                               ['Local_10pct_mean_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_mean_DOY']],
'Population_timing': [["Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                                "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv"],
                              'RQ_Pred_YYY_Local_sample', ['0.1', '0.5', '0.9'],         
                              ['Local_10pct_onset_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_termination_DOY']]}

summary_list = Onset_termination_eval(out_path = "Data/Simulated_Distribution_Models/Summaries/Noise10_", 
                                      model_dict = model_dict,
                                     sample_counts = [50, 100, 200, 300, 400, 500, 600, 700, 800, 900, 1000], sample_type = 'normal')
summary_data = summary_list[0]
r2_summary = summary_list[2]

__________________________indiv_timing____________________________________
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Sl

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
['0.1', '0.5', '0.9']
__________________________Population_mean_timing____________________________________
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distri

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
['0.1', '0.5', '0.9']
__________________________indiv_timing____________________________________
Data\Simulated

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Sim

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_S

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_S

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
['0.1', '0.5', '0.9']
__________________________indiv_timing____________________________________
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distr

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise10_RQ_Predict_Test_si

In [14]:
#create summary estimates of accuracy for models constructed using s individuals with moderate noise in the phenological variation in population median flowering dates
#and a bias towards collection of specimens proximate to theire individual mean flowering date

model_dict = {'indiv_timing': [["Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                                "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv"],
                               'RQ_Pred_YYY_Local_sample', ['0.1', '0.5', '0.9'], 
                               ['Local_indiv_onset_DOY', 'Local_indiv_mean_DOY', 'Local_indiv_termination_DOY']],
             'Population_mean_timing': [["Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                                "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv"],
                               'RQ_Pred_YYY_Local_sample', ['0.1', '0.5', '0.9'],
                               ['Local_10pct_mean_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_mean_DOY']],
'Population_timing': [["Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                                "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv",
                               "Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv"],
                              'RQ_Pred_YYY_Local_sample', ['0.1', '0.5', '0.9'],         
                              ['Local_10pct_onset_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_termination_DOY']]}

summary_list = Onset_termination_eval(out_path = "Data/Simulated_Distribution_Models/Summaries/Noise30_", 
                                      model_dict = model_dict,
                                     sample_counts = [50, 100, 200, 300, 400, 500, 600, 700, 800, 900, 1000], sample_type = 'normal')
summary_data = summary_list[0]
r2_summary = summary_list[2]

__________________________indiv_timing____________________________________
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Sl

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
['0.1', '0.5', '0.9']
__________________________Population_mean_timing____________________________________
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distributi

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data\Simu

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Sim

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_S

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
['0.1', '0.5', '0.9']
__________________________Population_mean_timing____________________________________
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variableduration_noise30_RQ_Predict_Test_si

Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample.csv
Data\Simulated_Distribution_Models/RQ_SimHerb_XXX_Simulated_Distribution_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribu

In [3]:
#create summary estimates of accuracy for models constructed using individuals with mild noise in the phenological variation in population median flowering dates
#and a bias twoards collection if specimens from late in the flowering period of the individual being sampled

model_dict = {'indiv_timing': [["Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                                "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv"],
                               'RQ_Pred_YYY_Local_sample_rightDist', ['0.1', '0.5', '0.9'], 
                               ['Local_indiv_onset_DOY', 'Local_indiv_mean_DOY', 'Local_indiv_termination_DOY']],
             'Population_mean_timing': [["Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                                "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv"],
                               'RQ_Pred_YYY_Local_sample_rightDist', ['0.1', '0.5', '0.9'],
                               ['Local_10pct_mean_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_mean_DOY']],
'Population_timing': [["Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                                "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv"],
                              'RQ_Pred_YYY_Local_sample_rightDist', ['0.1', '0.5', '0.9'],         
                              ['Local_10pct_onset_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_termination_DOY']]}

summary_list = Onset_termination_eval(out_path = "Data/Simulated_Distribution_Models/Summaries/RightDist_", 
                                      model_dict = model_dict,
                                     sample_counts = [50, 100, 200, 300, 400, 500, 600, 700, 800, 900, 1000], sample_type = 'right_skew')
summary_data = summary_list[0]
r2_summary = summary_list[2]

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_noise10_RQ_Predic

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_ri

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_S

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
['0.1', '0.5', '0.9']
__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Dist

__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_noise10_RQ_Pred

...

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_S

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribut

__________________________Population_timing____________________________________
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_noise10_RQ_Predict_T

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_ri

Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv
Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_S

In [5]:
#create summary estimates of accuracy for models constructed using s individuals with moderate noise in the phenological variation in population median flowering dates
#and a bias twoards collection if specimens from late in the flowering period of the individual being sampled

model_dict = {'indiv_timing': [["Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                                "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv"],
                               'RQ_Pred_YYY_Local_sample_rightDist', ['0.1', '0.5', '0.9'], 
                               ['Local_indiv_onset_DOY', 'Local_indiv_mean_DOY', 'Local_indiv_termination_DOY']],
             'Population_mean_timing': [["Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                                "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv"],
                               'RQ_Pred_YYY_Local_sample_rightDist', ['0.1', '0.5', '0.9'],
                               ['Local_10pct_mean_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_mean_DOY']],
'Population_timing': [["Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                                "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv",
                               "Data/Simulated_Distribution_rightDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_rightDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_rightDist.csv"],
                              'RQ_Pred_YYY_Local_sample_rightDist', ['0.1', '0.5', '0.9'],         
                              ['Local_10pct_onset_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_termination_DOY']]}

summary_list = Onset_termination_eval(out_path = "Data/Simulated_Distribution_Models/Summaries/RightDist_Noise30_", 
                                      model_dict = model_dict,
                                     sample_counts = [50, 100, 200, 300, 400, 500, 600, 700, 800, 900, 1000], sample_type = 'right_skew')
summary_data = summary_list[0]
r2_summary = summary_list[2]

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.c

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
['0.1', '0.5', '0.9']
__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Dis

__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simDa

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.c

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribu

__________________________Population_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Si

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.c

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
['0.1', '0.5', '0.9']
__________________________indiv_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData

In [6]:
#create summary estimates of accuracy for models constructed using individuals with mild noise in the phenological variation in population median flowering dates
#and a bias twoards collection if specimens from early in the flowering period of the individual being sampled

model_dict = {'indiv_timing': [["Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                                "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv"],
                               'RQ_Pred_YYY_Local_sample_leftDist', ['0.1', '0.5', '0.9'], 
                               ['Local_indiv_onset_DOY', 'Local_indiv_mean_DOY', 'Local_indiv_termination_DOY']],
             'Population_mean_timing': [["Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                                "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv"],
                               'RQ_Pred_YYY_Local_sample_leftDist', ['0.1', '0.5', '0.9'],
                               ['Local_10pct_mean_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_mean_DOY']],
'Population_timing': [["Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                                "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv"],
                              'RQ_Pred_YYY_Local_sample_leftDist', ['0.1', '0.5', '0.9'],         
                              ['Local_10pct_onset_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_termination_DOY']]}

summary_list = Onset_termination_eval(out_path = "Data/Simulated_Distribution_Models/Summaries/LeftDist_Noise10_", 
                                      model_dict = model_dict,
                                     sample_counts = [50, 100, 200, 300, 400, 500, 600, 700, 800, 900, 1000], sample_type = 'left_skew')
summary_data = summary_list[0]
r2_summary = summary_list[2]

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_l

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
['0.1', '0.5', '0.9']
__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_left

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_l

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribu

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.c

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
['0.1', '0.5', '0.9']
__________________________indiv_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData

In [7]:
#create summary estimates of accuracy for models constructed using individuals with moderate noise in the phenological variation in population median flowering dates
#and a bias twoards collection if specimens from early in the flowering period of the individual being sampled

model_dict = {'indiv_timing': [["Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                                "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv"],
                               'RQ_Pred_YYY_Local_sample_leftDist', ['0.1', '0.5', '0.9'], 
                               ['Local_indiv_onset_DOY', 'Local_indiv_mean_DOY', 'Local_indiv_termination_DOY']],
             'Population_mean_timing': [["Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                                "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv"],
                               'RQ_Pred_YYY_Local_sample_leftDist', ['0.1', '0.5', '0.9'],
                               ['Local_10pct_mean_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_mean_DOY']],
'Population_timing': [["Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                                "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv",
                               "Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv"],
                              'RQ_Pred_YYY_Local_sample_leftDist', ['0.1', '0.5', '0.9'],         
                              ['Local_10pct_onset_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_termination_DOY']]}

summary_list = Onset_termination_eval(out_path = "Data/Simulated_Distribution_Models/Summaries/LeftDist_Noise30_", 
                                      model_dict = model_dict,
                                     sample_counts = [50, 100, 200, 300, 400, 500, 600, 700, 800, 900, 1000], sample_type = 'left_skew')
summary_data = summary_list[0]
r2_summary = summary_list[2]

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.c

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
['0.1', '0.5', '0.9']
__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Dis

__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise30_RQ_Predict_Test_simDa

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.c

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribu

__________________________Population_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Si

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.c

Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
['0.1', '0.5', '0.9']
__________________________indiv_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_leftDist.csv
Data/Simulated_Distribution_leftDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_leftDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData

In [8]:
#create summary estimates of accuracy for models constructed using individuals with mild noise in the phenological variation in population median flowering dates
#and no collection bias

model_dict = {'indiv_timing': [["Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                                "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv"],
                               'RQ_Pred_YYY_Local_sample_flatDist', ['0.1', '0.5', '0.9'], 
                               ['Local_indiv_onset_DOY', 'Local_indiv_mean_DOY', 'Local_indiv_termination_DOY']],
             'Population_mean_timing': [["Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                                "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv"],
                               'RQ_Pred_YYY_Local_sample_flatDist', ['0.1', '0.5', '0.9'],
                               ['Local_10pct_mean_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_mean_DOY']],
'Population_timing': [["Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                                "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv"],
                              'RQ_Pred_YYY_Local_sample_flatDist', ['0.1', '0.5', '0.9'],         
                              ['Local_10pct_onset_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_termination_DOY']]}

summary_list = Onset_termination_eval(out_path = "Data/Simulated_Distribution_Models/Summaries/FlatDist_Noise10_", 
                                      model_dict = model_dict,
                                     sample_counts = [50, 100, 200, 300, 400, 500, 600, 700, 800, 900, 1000], sample_type = 'flat_skew')
summary_data = summary_list[0]
r2_summary = summary_list[2]

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.c

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
['0.1', '0.5', '0.9']
__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Dis

__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise10_RQ_Predict_Test_simDa

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.c

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribu

__________________________Population_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Si

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.c

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
['0.1', '0.5', '0.9']
__________________________indiv_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise10_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise10_RQ_Predict_Test_simData

In [9]:
#create summary estimates of accuracy for models constructed using individuals with mild noise in the phenological variation in population median flowering dates
#and no collection bias

model_dict = {'indiv_timing': [["Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                                "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv"],
                               'RQ_Pred_YYY_Local_sample_flatDist', ['0.1', '0.5', '0.9'], 
                               ['Local_indiv_onset_DOY', 'Local_indiv_mean_DOY', 'Local_indiv_termination_DOY']],
             'Population_mean_timing': [["Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                                "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv"],
                               'RQ_Pred_YYY_Local_sample_flatDist', ['0.1', '0.5', '0.9'],
                               ['Local_10pct_mean_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_mean_DOY']],
'Population_timing': [["Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                                "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv",
                               "Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv"],
                              'RQ_Pred_YYY_Local_sample_flatDist', ['0.1', '0.5', '0.9'],         
                              ['Local_10pct_onset_DOY', 'Local_50pct_mean_DOY', 'Local_90pct_termination_DOY']]}

summary_list = Onset_termination_eval(out_path = "Data/Simulated_Distribution_Models/Summaries/FlatDist_Noise30_", 
                                      model_dict = model_dict,
                                     sample_counts = [50, 100, 200, 300, 400, 500, 600, 700, 800, 900, 1000], sample_type = 'flat_skew')
summary_data = summary_list[0]
r2_summary = summary_list[2]

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.c

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
['0.1', '0.5', '0.9']
__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Dis

__________________________Population_mean_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise30_RQ_Predict_Test_simDa

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.c

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
['0.1', '0.5', '0.9']
__________________________Population_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribu

__________________________Population_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Si

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.c

Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variablesigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_variableduration_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
['0.1', '0.5', '0.9']
__________________________indiv_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_

__________________________indiv_timing____________________________________
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope8_10sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope1_30sigma_noise30_RQ_Predict_Test_simData_Simulated_Distribution_SlopeComp_Local_sample_flatDist.csv
Data/Simulated_Distribution_flatDist_Models/RQ_SimHerb_XXX_Simulated_Distribution_flatDist_Slope4_30sigma_noise30_RQ_Predict_Test_simData